# Imports

In [1]:
from RobinRollandModel.datautils import TipGenerator, visualize, collect_output, visualize_evaporation
from RobinRollandModel.main import RRModel
import RobinRollandModel.pyironjob
from pyiron_atomistics import Project
import numpy as np
import matplotlib.pyplot as plt
import plotly.graph_objects as go

In [3]:
# create a project folder
pr = Project("Example")

# Creating a tip for simulation

In [4]:
# a basic structure from which tip will be created
structure = pr.create.structure.bulk('Al','fcc',4.01,cubic=True)

In [5]:
# visualization outside pyiron
visualize(structure)

In [6]:
# Creates a tip generator object based on height, radius and zheight (a cut of value for atoms height, below which charge of atoms is set to zero)
tip = TipGenerator(structure,h=80,ah=20,zheight=50)

In [7]:
# creates tip as a pyiron structure
pr_tip = tip.create_tip_pyiron(pr)

In [8]:
visualize(pr_tip)


In [9]:
pr_tip.plot3d(mode='plotly')

In [10]:
#tip generator object for shanked specimens
tip_shank = TipGenerator(structure=structure,h=80,ah=30,alpha=10,zheight=50)

In [11]:
pr_tip_shank = tip_shank.create_tip_pyiron(pr)

In [12]:
visualize(pr_tip_shank)

In [13]:
pr_tip_shank.plot3d(mode='plotly')

# Charge equilibration

In [14]:
al_apt_sim = RRModel(tip_generator=tip,structure=pr_tip,e_field=4)

In [15]:
tip_output_al = al_apt_sim.charge_distribution_z(structure=pr_tip,e_field=4,radius=20,steps=1000,epsilon=1e-9)

In [16]:
visualize(pr_tip,charge=tip_output_al['final_charge'],surf_indices=tip_output_al['surface_indices'])

In [17]:
al_apt_shank = RRModel(tip_generator=tip_shank,structure=pr_tip_shank,e_field=4)

In [18]:
tip_output_al_shank = al_apt_shank.charge_distribution_z(structure=pr_tip_shank,e_field=4,radius=20,steps=1000,epsilon=1e-9)

In [19]:
visualize(pr_tip_shank,charge=tip_output_al_shank['final_charge'],surf_indices=tip_output_al_shank['surface_indices'])

# Trajectory Simulation 

In [20]:
evap = al_apt_shank.evaporation_trajectory_force_cut(pr_tip_shank, tip_output_al_shank['surface_indices'], tip_output_al_shank['final_charge'], evap_ind=np.argmax(tip_output_al_shank['maxwell_stress']), dt=1)

# pyiron implementation

In [20]:
pr = Project("Example_pyiron")

In [21]:
test = pr.create.job.RRModelAPTjob('test',delete_existing_job=True)

In [22]:
structure = pr.create.structure.bulk('Al','fcc',4.01,cubic=True)

In [23]:
test.input.basic_structure = structure
test.input.e_field = 4
test.input.tip_height = 80
test.input.tip_radius = 20
test.input.z_height = 50
test.input.num_atoms = 10
test.input.tip_shank_angle = 5

In [24]:
tipg = test.create_input_structure()

In [25]:
test.input.structure.plot3d(scalar_field=test.input.structure.positions[:,2],mode='plotly')

In [26]:
test.run()

The job test was saved and received the ID: 1


100%|██████████| 10/10 [00:03<00:00,  3.04it/s]


In [27]:
pr.job_table()

id    status chemicalformula   job subjob projectpath  \
0   1  finished            None  test  /test        None   

                                                          project  \
0  /Users/shyamkatnagallu/Projects/APTrajectories/Example_pyiron/   

                   timestart timestop totalcputime  \
0 2024-03-14 14:34:39.199990     None         None   

                        computer       hamilton hamversion parentid masterid  
0  pyiron@shyams-mbp-2.mpie.de#1  RRModelAPTjob        0.4     None     None

In [28]:
tj = pr.load('test')

In [63]:
trajectories =  tj.output.evaporation_trajectories